In [1]:
#!/usr/bin/env python
# -*- coding: UTF-8

# Parsing HTML from `wget` run!

## Initializing

In [62]:
# import necessary libraries
import os, re # for navigating file trees and working with strings
import csv # for reading in CSV files
from glob import glob # for finding files within nested folders
import json, pickle # For saving a loading dictionaries, etc. from file with JSON and pickle formats
from datetime import datetime # For timestamping files
from nltk.stem.porter import PorterStemmer # an approximate method of stemming words
stemmer = PorterStemmer()
from nltk import word_tokenize, sent_tokenize # widely used text tokenizer
import urllib, urllib.request # for testing pages

# Import parser
from bs4 import BeautifulSoup # BS reads and parses even poorly/unreliably coded HTML 
from bs4.element import Comment # helps with detecting inline/junk tags when parsing with BS
import lxml # for fast HTML parsing with BS


In [3]:
inline_tags = ["b", "big", "i", "small", "tt", "abbr", "acronym", "cite", "dfn",
               "em", "kbd", "strong", "samp", "var", "bdo", "map", "object", "q",
               "span", "sub", "sup"] # this list helps with eliminating junk tags when parsing HTML

Debug = True # Set to "True" for extra progress reports while algorithms run
notebook = True # Use different file paths depending on whether files are being accessed from shell (False) or within a Jupyter notebook (True)

# Set parser for BeautifulSoup to use depending on whether code is running in notebook or not 
# (notebooks don't have faster lxml parser installed)
if notebook:
    bsparser = "html.parser"
else:
    bsparser = "lxml"

In [72]:
# ### Set directories

if notebook:
    wget_dataloc = "/home/jovyan/work/wget/parll_wget/" #data location for schools downloaded with wget in parallel
    micro_sample13 = "/home/jovyan/work/Charter-school-identities/data/micro-sample13_coded.csv" #data location for random micro-sample of 300 US charter schools
    full_schooldata = "/home/jovyan/work/Charter-school-identities/data/charter_URLs_2014.csv" #data location for 2014 population of US charter schools
    save_dir = "/home/jovyan/work/Charter-school-identities/data/"

else:
    wget_dataloc = "/vol_b/data/wget/parll_wget/" #data location for schools downloaded with wget in parallel
    micro_sample13 = "/vol_b/data/Charter-school-identities/data/micro-sample13_coded.csv" #data location for random micro-sample of 300 US charter schools
    full_schooldata = "/vol_b/data/Charter-school-identities/data/charter_URLs_2014.csv" #data location for 2014 population of US charter schools
    save_dir = "/vol_b/data/Charter-school-identities/data/"

example_page = "https://westlakecharter.com/about/"
example_schoolname = "TWENTY-FIRST_CENTURY_NM"
example_folder = wget_dataloc + "TWENTY-FIRST_CENTURY_NM/"
example_file = example_folder + "21stcenturypa.com/wp/default?page_id=27.tmp.html"


In [5]:
# ### Set parsing keywords

keywords = ['values', 'academics', 'skills', 'purpose',
                       'direction', 'mission', 'vision', 'vision', 'mission', 'our purpose',
                       'our ideals', 'ideals', 'our cause', 'curriculum','curricular',
                       'method', 'pedagogy', 'pedagogical', 'approach', 'model', 'system',
                       'structure','philosophy', 'philosophical', 'beliefs', 'believe',
                       'principles', 'creed', 'credo', 'values','moral', 'history', 'our story',
                       'the story', 'school story', 'background', 'founding', 'founded',
                       'established','establishment', 'our school began', 'we began',
                       'doors opened', 'school opened', 'about us', 'our school', 'who we are',
                       'our identity', 'profile', 'highlights']

mission_keywords = ['mission','vision', 'vision:', 'mission:', 'our purpose', 'our ideals', 'ideals:', 'our cause', 'cause:', 'goals', 'objective']
curriculum_keywords = ['curriculum', 'curricular', 'program', 'method', 'pedagogy', 'pedagogical', 'approach', 'model', 'system', 'structure']
philosophy_keywords = ['philosophy', 'philosophical', 'beliefs', 'believe', 'principles', 'creed', 'credo', 'value',  'moral']
history_keywords = ['history', 'story','our story', 'the story', 'school story', 'background', 'founding', 'founded', 'established', 'establishment', 'our school began', 'we began', 'doors opened', 'school opened']
about_keywords =  ['about us', 'our school', 'who we are', 'overview', 'general information', 'our identity', 'profile', 'highlights']

mission_keywords = set(stemmer.stem(word) for word in mission_keywords)
curriculum_keywords = set(stemmer.stem(word) for word in curriculum_keywords)
philosophy_keywords = set(stemmer.stem(word) for word in philosophy_keywords)
history_keywords = set(stemmer.stem(word) for word in history_keywords)
about_keywords =  set(stemmer.stem(word) for word in about_keywords)


In [51]:
# ### Define (non-parsing) helper functions

def get_vars(data):
    """Defines variable names based on the data source called."""
    
    if data==full_schooldata:
        URL_variable = "TRUE_URL"
        NAME_variable = "SCH_NAME"
        ADDR_variable = "ADDRESS"
    
    elif data==micro_sample13:
        URL_variable = "URL"
        NAME_variable = "SCHNAM"
        ADDR_variable = "ADDRESS"
    
    else:
        try:
            print("Error processing variables from data file " + str(data) + "!")
        except Exception as e:
            print(e)
            print("ERROR: No data source established!\n")
    
    return(URL_variable,NAME_variable,ADDR_variable)


def tag_visible(element):
    """Returns false if a web element has a non-visible tag, 
    i.e. one site visitors wouldn't actually read--and thus one we don't want to parse"""
    
    if element.parent.name in ['style', 'script', 'head', 'title', 'meta', '[document]']:
        return False
    if isinstance(element, Comment):
        return False
    return True


def webtext_from_files(datalocation):
    """Concatenate and return a single string from all webtext (with .txt format) in datalocation"""
    
    string = ""
    for root, dirs, files in os.walk(datalocation):
        for file in files:
            if file.endswith(".txt"):
                fileloc = open(datalocation+file, "r")
                string = string + (fileloc.read())
    return string


def remove_spaces(file_path):
    """Remove spaces from text file at file_path"""
    
    words = [x for x in open(file_path).read().split() if x != ""]
    text = ""
    for word in words:
        text += word + " "
    return text


def save_to_file(dicts_list, file, mode):
    """Saves dicts_list to file using JSON or pickle format (whichever was specified)."""
    
    file = str(file)
    
    try:
        if mode=="JSON":
            if not file.endswith(".json"):
                file += ".json"
            with open(file, 'wb') as outfile:
                json.dump(dicts_list, outfile)
            #pickle.dump(dicts_list, outfile)
                print(dicts_list + " successfully saved to " + file + "in JSON format!\n")

        elif mode=="pickle":
            if not file.endswith(".pickle"):
                file += ".pickle"
            with open(file, 'wb') as outfile:
                pickle.dump(dicts_list, outfile)
                print(dicts_list + " successfully saved to " + file + " in pickle format!\n")

        else:
            print("ERROR! Save failed due to improper arguments. These are: file, object to be saved, and file format to save in.\n
                  Specify either 'JSON' or 'pickle' as third argument ('mode' or file format) when calling this function.")
    
    except Exception as e:
        print(e)
    

def load_json(file):
    """Loads dicts_list (or whatever) from file, using either JSON or pickle format. 
    The created object should be assigned when called."""
    
    file = str(file)
    
    with open(file,'rb') as infile:
        if file.endswith(".json"):
            var = json.load(infile)
        if file.endswith(".pickle"):
            var = pickle.load(infile)
        print(file + " successfully loaded!\n")
    return var


SyntaxError: invalid syntax (<ipython-input-51-372b8fa7823e>, line 63)

In [7]:
# ### Compare parsing by newlines vs. by HTML tags

def parseurl_by_newlines(urlstring):
    """Uses BS to parse HTML from a given URL and looks for three newlines to separate chunks of text."""
    
    # Read HTML from a given url:
    with urllib.request.urlopen(urlstring) as url:
        s = url.read()
    
    # Parse raw text from website body:
    soup = BeautifulSoup(s, bsparser)
    texts = soup.findAll(text=True)
    visible_texts = filter(tag_visible, texts)  
    webtext = u" ".join(t.strip() for t in visible_texts)
    
    return re.split(r'\s{3,}', webtext)


def parseurl_by_tags(urlstring):
    """Cleans HTML by removing inline tags, ripping out non-visible tags, 
    replacing paragraph tags with a random string, and finally using this to separate HTML into chunks.
    Reads in HTML from the web using a given website address, urlstring."""
    
    with urllib.request.urlopen(urlstring) as url:
        HTML_page = url.read()

    random_string = "".join(map(chr, os.urandom(75))) # Create random string for tag delimiter
    soup = BeautifulSoup(HTML_page, bsparser)
    
    [s.extract() for s in soup(['style', 'script', 'head', 'title', 'meta', '[document]'])] # Remove non-visible tags
    for it in inline_tags:
        [s.extract() for s in soup("</" + it + ">")] # Remove inline tags
    
    visible_text = soup.getText(random_string).replace("\n", "") # Replace "p" tags with random string, eliminate newlines
    visible_text = list(elem.replace("\t","") for elem in visible_text.split(random_string)) # Split text into list using random string while eliminating tabs
    visible_text = list(filter(lambda vt: vt.split() != [], visible_text)) # Eliminate empty elements
    # Consider joining list elements together with newline in between by prepending with: "\n".join
    
    return(visible_text)


# Text chunking accuracy of parsing by tags is superior to parsing by newlines:
# Compare each of these with the browser-displayed content of example_page:
if Debug:
    print(parseurl_by_newlines(example_page),"\n\n",parseurl_by_tags(example_page))
    

['', 'Contact Us: 2680 Mabry Dr. 95835 (916) 567-5760 | admin@westlakecharter.com', 'Staff Login', 'About', 'Administration & Support Staff  Employment Opportunities  Business Services  Admission & Enrollment Information  Supply Donations  Hot Lunch Payments  Hot Lunch Menu', 'Board', 'Board Policies  Board Committees  Board Documents', 'WCS', 'Infinite Campus Login  School Dismissal Manager  Ways to Westlake', 'Teachers  BASE  WAVE', 'Meetings  Contact Us  Volunteer Opportunities  Volunteer Hours  Log Volunteer Hours  Spirit Store', 'Calendars', '17/18 School Calendar  18/19 School Calendar', 'About', 'About  Aimee Wells  2013-09-18T18:36:35+00:00', 'About Westlake Charter Schools  Key School Features', 'International Focus  Thematic Curriculum  Artistic Development  Foreign Language Instruction  School-Wide Enrichment Model', 'Core Values', 'Respect  Excellence  Responsibility  Reflective  Global Perspective  Stewardship  Perseverance  Inquisitive  Joyful Learning  Gratitude', 'Calen

In [8]:
# ### Define parsing helper functions

def parsefile_by_tags(HTML_file):
    
    """Cleans HTML by removing inline tags, ripping out non-visible tags, 
    replacing paragraph tags with a random string, and finally using this to separate HTML into chunks.
    Reads in HTML from storage using a given filename, HTML_file."""

    random_string = "".join(map(chr, os.urandom(75))) # Create random string for tag delimiter
    soup = BeautifulSoup(open(HTML_file), bsparser)
    
    [s.extract() for s in soup(['style', 'script', 'head', 'title', 'meta', '[document]'])] # Remove non-visible tags
    for it in inline_tags:
        [s.extract() for s in soup("</" + it + ">")] # Remove inline tags
    
    visible_text = soup.getText(random_string).replace("\n", "") # Replace "p" tags with random string, eliminate newlines
    visible_text = list(elem.replace("\t","") for elem in visible_text.split(random_string)) # Split text into list using random string while eliminating tabs
    visible_text = list(filter(lambda vt: vt.split() != [], visible_text)) # Eliminate empty elements
    # Consider joining list elements together with newline in between by prepending with: "\n".join

    return(visible_text)


In [9]:
if Debug:
    example_textlist = parsefile_by_tags(example_file)
    print("Output of parsefile_by_tags:\n\n", example_textlist, "\n\n")


Output of parsefile_by_tags:

 ['About', 'Administration', 'Admissions', 'News', 'Charter School Information', 'Location', 'Frequently Asked Questions', 'Photos/Videos', 'School Facebook Page', 'Financial Reports', 'Nondiscrimination Policy', 'Academics', '5th Grade', '6th Grade', '7th Grade', '8th Grade', 'Associated Arts', 'Summer Reading >>', '5th Grade Reading List', '6th Grade Reading List', '7th Grade Reading List', '8th Grade Reading List', 'Parents', 'General Information', 'School Calendar >>', 'Download Calendar', 'PlusPortals', 'Before & After School Care', 'Forms >>', 'New Student Registration Packet', 'Free and Reduced Lunch', 'Student Handbook', 'School Uniform Order Form', 'School Supplies >>', '5th Grade', '6th Grade', '7th Grade', '8th Grade', 'Food Menu', 'PARCC', 'Inclement Weather Schedule', 'West Side Bus Routes', 'Athletics', 'Coach Contact Info', 'Athletics Schedule', 'Sports News', 'Sports Release', 'Physical Form', 'Student Athlete Contract', 'Student Athlete Gr

In [10]:
def filter_keywords_page(pagetext_list):
    
    """Filters webtext of a given .html page, which is parsed and in list format, to only those strings 
    within pagetext_list containing an element (word or words) of a previously defined list of meaningful keywords."""
    
    validcharacters = [' ', '.', '?']
    filteredtext = []  
    
    for string in pagetext_list:
        lowercasestring = string.lower()
        for key in keywords:
            if key in lowercasestring:
                if key in lowercasestring.split(' '): #check that the word is the whole word not part of another one
                    filteredtext.extend([string.lower()])

    filteredtext = list(set(filteredtext))
    finaltext = []
    for x in filteredtext:
        finaltext.append(x.replace('\xa0', " ")) # Clean up any remaining (non-readable) unicode
    return finaltext


In [11]:
if Debug:
    print("Output of filter_keywords_page:\n\n", filter_page(example_textlist), "\n\n")


Output of filter_page:

 ['history', 'it is the mission of 21st century public academy to continually search for positive learning experiences that enrich students and staff. whenever possible, these lessons will take place in the arena in which they are practiced.', '21st century is a charter middle school. we have been a school since 2000. we serve a diverse population of nearly 70 students per grade. all staff bring years of teaching experience into our classrooms, and many have worked together in other settings. we emphasize the core curriculum of math, science, social studies, and language arts, as well as learning experiences in the community, city, and state. two associated arts courses are offered to each student every semester, including music and media programs.', 'vision', 'academics', 'mission'] 




In [81]:
def remove_overlaps(folder_path, schoolname):
    
    """Filters out overlapping parts of each page, returning combined list of non-redundant text elements from all pages.
    Removes superfluous text elements common to multiple pages at either the beginning or end: namely,
    this eliminates menus, headers, and footers, which are redundant elements not useful for analysis. 
    
    We do this by making one pass through all the pages, in which we store text and eliminate duplicate pages.
    We store the text both forwards (start to end) and backwards (end to start), 
    in order to find duplicate headers (or menus) and footers, respectively.
    Then, we do a second pass through the text to find the longest common headers and footers and remove them from each page."""
    
    #num_pages = len([f for f in os.listdir(folder_path) if f[0] != "."])
    list_pages = [file for file in glob(folder_path + "**", recursive=True) if file.endswith(".html")] # Keep only HTML files
    num_pages = len(list_pages)
    pages, reverse_pages, pages_set, filtered_site_text = [], [], set(), []
    
    # First iterate through each page to find overlaps
    for file in list_pages:

        page_text = "\n".join(parsefile_by_tags(file)) # Parse HTML in file, join into string via newlines

        # Check if page is a duplicate. If so, store it only as an empty file. 
        # As compared to ignoring these pages completely, storing as empty preserves the num_pages count.
        if page_text in pages_set:
            pages.append("")
            reverse_pages.append("")
            continue

        pages.append(page_text) # Save pages in this list going forwards, from start to end. Use this to eliminate headers
        reverse_pages.append(page_text[::-1]) # Save pages in this list going forwards, from end to start. Use this to eliminate footers
        pages_set.add(page_text) # Save pages to a set. Use this to check for duplicates

    # Iterate again through each page to only keep non-overlapping phrases
    for i in range(len(pages)):
        
        try:
            # Initialize indices: start_index indicates how many characters into a page, 
            #  from start to end, is shared with at least one other page (forwards). 
            # end_index indicates the same, but from end to start (backwards).
            start_index, end_index = -1, -1 
            filtered_page_text = "" # Initialize text string holding the full site text with all overlaps removed from each page

            filtered_page_text = pages[i]

            # Find longest number of characters shared by this file and at least one other by going forwards, i.e. from start to end:
            start_index = max([len(os.path.commonprefix([pages[i], pages[j]])) \
                               for j in range(len(pages)) if i != j]) 
            if start_index != 0:
                # Round down start_index to beginning of current word
                while start_index > 0 and filtered_page_text[start_index] != " ":
                    start_index -=1
                if filtered_page_text[start_index] == " ":
                    start_index += 1
                filtered_page_text = filtered_page_text[start_index:]

            # Find longest number of characters shared by this file and at least one other by going backwards, i.e. from end to start:
            end_index = max([len(os.path.commonprefix([reverse_pages[i], reverse_pages[j]]))\
                             for j in range(len(reverse_pages)) if i != j])
            if end_index != 0:
                # Round up end_index to end of current word
                while end_index >= 0 and filtered_page_text[-end_index] != " ":
                    end_index -=1
                filtered_page_text = filtered_page_text[:-end_index]

            if Debug and filtered_page_text != "":
                print("\n    Removed overlaps for HTML page #" + str(i) + " of " + str(len(pages)) + ", which is probably " + \
                "this file:\n    " + str(list_pages[i]) + "\n    and contains the following text:\n")
                print(filtered_page_text)

            filtered_site_text.extend(filtered_page_text + " ") # Add the filtered_page_text (all overlaps removed) to long string of site text
        
        except Exception as e:
            print("    ERROR! Encountered this exception:",e)

    print("Successfully removed menus, headers, and footers and merged all HTML pages for " + str(schoolname) + "!\n")
    return filtered_site_text


In [ ]:
if Debug:
    print("Output of remove_overlaps:\n\n", remove_overlaps(example_folder, example_schoolname), "\n\n")
    


    Removed overlaps for HTML page #0 of 880, which is probably this file:
    /home/jovyan/work/wget/parll_wget/TWENTY-FIRST_CENTURY_NM/21stcenturypa.com/wp/default?author=1.tmp.html
    and contains the following text:

21stadmin
You are here:
Home
/
21stadmin
About 
21stadmin
This author has yet to write their bio.
Meanwhile lets just say that we are proud 
21stadmin
 contributed a whooping 342 entries.
Entries by 21stadmin
6th Grade OSI to the Petroglyphs
December 13, 2017
/
in 
Photos/Videos
/
by 
21stadmin
Spelling Bee
December 8, 2017
/
in 
Photos/Videos
, 
Uncategorized
/
by 
21stadmin
Science Bowl Competition
December 7, 2017
/
in 
Photos/Videos
/
by 
21stadmin
Governance Council Resolution No. 12-7- 2017
December 6, 2017
/
in 
Governance Council Agenda
/
by 
21stadmin
Resolution: To reject the offered contract of Realtors Association of New Mexico General Amendment 2-2017 between Reginald L. Olson, Exp Realty, LLC and 21 st Century Public Academy and propose counter offer of


    Removed overlaps for HTML page #4 of 880, which is probably this file:
    /home/jovyan/work/wget/parll_wget/TWENTY-FIRST_CENTURY_NM/21stcenturypa.com/wp/default?p=1396.tmp.html
    and contains the following text:

here:
Home
/
PTA
/
“Living Classroom” Project
“Living Classroom” Project
May 5, 2015
/
in 
PTA
/
by 
21stadmin
The 21
st
 Century PTA is planning a “living classroom” for our school – and we need your help!
The project is to turn the large dirt and rock area between the parking lot and street into a green space with fruit trees, planter boxes, a garden space, and seating for outdoor instruction. Our science teachers are planning classes for this.
The first step is clearing off the existing rock and dirt and leveling the area.  Do you know anyone with a bobcat? We need a truck to haul away rock and excess dirt. The next step will be installing underground watering – fortunately there is already a water valve where we need it.  We will need volunteers to help plan, dig, 




    Removed overlaps for HTML page #14 of 880, which is probably this file:
    /home/jovyan/work/wget/parll_wget/TWENTY-FIRST_CENTURY_NM/21stcenturypa.com/wp/default?page=5&paged=66.tmp.html
    and contains the following text:



    Removed overlaps for HTML page #15 of 880, which is probably this file:
    /home/jovyan/work/wget/parll_wget/TWENTY-FIRST_CENTURY_NM/21stcenturypa.com/wp/default?attachment_id=635.tmp.html
    and contains the following text:

here:
Home
/
_DSC2347
_DSC2347
October

    Removed overlaps for HTML page #16 of 880, which is probably this file:
    /home/jovyan/work/wget/parll_wget/TWENTY-FIRST_CENTURY_NM/21stcenturypa.com/wp/default?page_id=47.tmp.html
    and contains the following text:

Minutes
Search
Administration
You are here:
Home
/
About
/
Administration
Small class sizes enable teachers to work more closely with each individual student. Teachers meet in grade level teams every day to coordinate with one another and to prepare collaborative les

Read

    Removed overlaps for HTML page #21 of 880, which is probably this file:
    /home/jovyan/work/wget/parll_wget/TWENTY-FIRST_CENTURY_NM/21stcenturypa.com/wp/default?p=2400.tmp.html
    and contains the following text:



    Removed overlaps for HTML page #22 of 880, which is probably this file:
    /home/jovyan/work/wget/parll_wget/TWENTY-FIRST_CENTURY_NM/21stcenturypa.com/wp/default?p=3987.tmp.html
    and contains the following text:

Minutes
Search
21st CPA Art Exhibit at State Fair
You are here:
Home
/
Uncategorized
/
21st CPA Art Exhibit at State Fair
School Hours
Regular School Hours:
8:15-3:40 Monday, Tuesday, Thursday, Friday
8:15-3:00 Wednesday
Students may not be dropped off prior to 8:00.
Recent News
6th Grade OSI to the Petroglyphs
(December 13, 2017)
Spelling Bee
(December 8, 2017)
Science Bowl Competition
(December 7, 2017)
Boys Basketball
(November 21, 2017)
5th Grade OSI to US Eagle Federal Credit Union
(November 15, 2017)
New West Side Bus Routes for 21stCPA



    Removed overlaps for HTML page #28 of 880, which is probably this file:
    /home/jovyan/work/wget/parll_wget/TWENTY-FIRST_CENTURY_NM/21stcenturypa.com/wp/default?p=1867.tmp.html
    and contains the following text:

Agenda
/
5/18/15 Governance Council Agenda
5/18/15 Governance Council Agenda
May 15, 2015
/
in 
Governance Council Agenda
/
by 
21stadmin
Call Meeting to Order
Roll Call
Approval of Minutes
Open Forum
# Student Uniform Policy Adjustment – Action Item and presentation by
       Clarissa Delgado
School Finances:
   Introduction of Michael Vigil, Finance Consultant
   Introduction of Rita Hershey COO
Financial Statements for Review
Balance Sheet Report – April 30, 2015
Account Summary Report – Revenues –April 30, 2015
Account Summary Report – Expenditures- April 30, 2015
Bank Reconciliation Reports for Review
April 2015
Cash Disbursements for Approval #
April 2015
Bars for Approval #
Maintenance BARs -none
Transfer BARs – none
Initial Budget  – none
RFR Update
RFR Summar

...


    Removed overlaps for HTML page #522 of 880, which is probably this file:
    /home/jovyan/work/wget/parll_wget/TWENTY-FIRST_CENTURY_NM/21stcenturypa.com/wp/default?m=201301.tmp.html
    and contains the following text:

2013
You are here:
Home
/
2013
/
January
1/29/13 Foundation Meeting
January 29, 2013
/
in 
Foundation Agenda
/
by 
21stadmin
Agenda:
January 29, 2012
5:30PM
Read more
  →
1/8/13 Governance Council Meeting
January 8, 2013
/
in 
Governance Council Agenda
/
by 
21stadmin
Agenda:
January 8,

    Removed overlaps for HTML page #523 of 880, which is probably this file:
    /home/jovyan/work/wget/parll_wget/TWENTY-FIRST_CENTURY_NM/21stcenturypa.com/wp/default?m=201504&paged=3.tmp.html
    and contains the following text:

3)
You are here:
Home
/
2015
/
April
Spring Fling Planning Meeting on April 29th
April 10, 2015
/
in 
PTA
/
by 
21stadmin
Spring Fling Planning Meeting
“The Dragon Olympics”
Wednesday, April 29
th
, 6:00 PM in the school cafeteria.
Everyone welcome. We n


    Removed overlaps for HTML page #534 of 880, which is probably this file:
    /home/jovyan/work/wget/parll_wget/TWENTY-FIRST_CENTURY_NM/21stcenturypa.com/wp/default?p=3798.tmp.html
    and contains the following text:

Agenda
/
Memorandum between 21stCPA and APS
Memorandum between 21stCPA and APS
March 30, 2017
/
in 
Governance Council Agenda
/
by 
21stadmin
MEMORANDUMM OF UNDERSTANDING
BETWEEN
21 ST CENTURY PUBLIC ACADEMY
AND
ALBUQUERQUE PUBLIC SCHOOLS
This MEMORANDUM OF UNDERSTANDING (MOU) is hereby made and entered into by
and between 21 st CENTURY PUBLIC ACADEMY (“School”) and ALBUQUERQUE
PUBLIC SCHOOLS (APS).
A. PURPOSE:
The purpose of this MOU is to undertake the first phase in the design, repair, maintenance and/
or improvement of land and charter school selected educational facilities as required by NMSA
1978 22-8A- 4.2 by establishing a method of distribution of the funds held by APS, solely as an
agent for disbursement, of said funds at the direction of 21 st Century Pub

Agenda
/
4/21/16 GC Agenda
4/21/16 GC Agenda
April 19, 2016
/
in 
Governance Council Agenda
/
by 
21stadmin
Call Meeting to Order
Roll Call
Approval of Minutes
Open Forum-
Public Input Invited on Items I, II & III
School Calendar 2016-2017*
Salary Schedule 2016-2017*
Operational budget 2016-2017*
Bars for Approval*
a.  Increase Bars-5
B. Maintenance Bars -2
C. Transfer Bars – 1
 V.      Approval for EOY clean-up*
VI.      Building Committee Report
VII.      Board Training
Viii.     Principal’s Report
Old Business:
Next Meeting:  TBD
Adjourn Open Meeting
(*) Action Item
– Budget Revenue Report FY16.17
– Budget Expenditure Report FY16.17
School Hours
Regular School Hours:
8:15-3:40 Monday, Tuesday, Thursday, Friday
8:15-3:00 Wednesday
Students may not be dropped off prior to 8:00.
Recent News
6th Grade OSI to the Petroglyphs
(December 13, 2017)
Spelling Bee
(December 8, 2017)
Science Bowl Competition
(December 7, 2017)
Boys Basketball
(November 21, 2017)
5th Grade OSI to US Eagle Federal

(Page 2)
You are here:
Home
/
2016
/
November
10/10 PTA Meeting Minutes
November 16, 2016
/
in 
PTA Agenda
/
by 
21stadmin
10/10/16 PTA Meeting Minutes
11/14 Basketball Announcements
November 14, 2016
/
in 
Sports
/
by 
21stadmin
Girls Basketball Game
When: 
Monday, Nov 14, 2016
Where: 
St. Charles Catholic School, 1801 Hazeldine Ave SE, Albuquerque, NM 87106, USA (
map
)
Description: 
JV @ 5:30p JV vs. St. Marys Belen Varsity @ 6:30p Varsity vs. St. Charles
Girls Basketball Game
When                 
Saturday, Nov 19, 2016
Where               Elite Sports Academy, 501 Main St NW, Albuquerque, NM 87104, USA (
map
)
Description      Varsity @ 2:30p
21st vs. Santa Fe Prep
Girls Basketball Game- 
(Last Game)
When: 
Tuesday, Nov 22, 2016
Where: 
Annunciation Catholic School, 2610 Utah St NE, Albuquerque, NM 87110, United States (
map
)
Description: 
JV @ 5:30p 21st vs. Annunciation Varsity @ 6:30p 21st vs Annunciation
PTA After School Enrichment Clubs
November 7, 2016
/
in 
PTA
/
by 
21sta

¬¦lvûQzIq{Rðö/ Ó22Z JwÛCfwêq½}¬~)ì.Ö¿M@3×¡è½Î8}§kü8³d«s¬¦lvûQzIq{Rðö/ Ó22Z JwÛCfwêq½}¬~)ì.Ö¿M@3×¡è½Î8}§kü8³d«s¬¦lvûQzIq{Rðö/ Ó22Z JwÛCfwêq½}¬~)ì.Ö¿M@3×¡è½Î8}§kü8³d«s¬¦lvûQzIq{Rðö/ Ó22Z JwÛCfwêq½}¬~)ì.Ö¿M@3×¡è½Î8}§kü8³d«s¬¦lvûQzIq{Rðö/ Ó22Z JwÛCfwêq½}¬~)ì.Ö¿M@3×¡è½Î8}§kü8³d«s¬¦lvûQzIq{Rðö/ Ó22Z JwÛCfwêq½}¬~)ì.Ö¿M@3×¡è½Î8}§kü8³d«s¬¦lvûQzIq{Rðö/ Ó22Z JwÛCfwêq½}¬~)ì.Ö¿M@3×¡è½Î8}§kü8³d«s¬¦lvûQzIq{Rðö/ Ó22Z JwÛCfwêq½}¬~)ì.Ö¿M@3×¡è½Î8}§kü8³d«s¬¦lvûQzIq{Rðö/ Ó22Z JwÛCfwêq½}¬~)ì.Ö¿M@3×¡è½Î8}§kü8³d«s¬¦lvûQzIq{Rðö/ Ó22Z JwÛCfwêq½}¬~)ì.Ö¿M@3×¡è½Î8}§kü8³d«sAbout¬¦lvûQzIq{Rðö/ Ó22Z JwÛCfwêq½}¬~)ì.Ö¿M@3×¡è½Î8}§kü8³d«s¬¦lvûQzIq{Rðö/ Ó22Z JwÛCfwêq½}¬~)ì.Ö¿M@3×¡è½Î8}§kü8³d«s¬¦lvûQzIq{Rðö/ Ó22Z JwÛCfwêq½}¬~)ì.Ö¿M@3×¡è½Î8}§kü8³d«sAdministration¬¦lvûQzIq{Rðö/

In [45]:
def categorize_page(pagetext_list): 
    
    """Takes in a list of all the relevant (filtered) text from a given webpage. 
    Categorizes each block of text by scoring based on keyword count, using already-defined lists 
    of keywords per category--mission, philosophy, curriculum, history, and "about"/general self-description."""
    
    mission_list = []
    curriculum_list = []
    philosophy_list = []
    history_list = []
    about_list = []
    
    for string in pagetext_list:
        mission_score, curriculum_score, philosophy_score, history_score, about_score = 0, 0, 0, 0, 0
        for word in mission_keywords:
            mission_score+=string.count(word)
            if 'mission' in string.lower():
                mission_score = 2
                
        for word in curriculum_keywords:
            curriculum_score+=string.count(word)
            if 'curriculum' in string.lower():
                curriculum_score = 2
                
        for word in philosophy_keywords:
            philosophy_score+=string.count(word)
            if 'philosophy' in string.lower() or 'value' in string.lower():
                philosophy_score = 2
        
        for word in history_keywords:
            history_score+=string.count(word)
            if 'history' in string.lower():
                history_score = 2
        
        for word in about_keywords:
            about_score+=string.count(word)
            if 'about us' in string.lower() or "about-us" in string.lower():
                about_score = 2
        
        if mission_score>=2:
            mission_list.append(string)
        if curriculum_score>=2:
            curriculum_list.append(string)
        if philosophy_score>=2:
            philosophy_list.append(string)
        if history_score>=2:
            history_list.append(string)
        if about_score>=2:
            about_list.append(string)
        elif (mission_score + curriculum_score + philosophy_score + history_score + about_score >=2):
            about_list.append(string)
        
    #return {'mission': mission_list, 'curriculum' : curriculum_list, 'philosophy': philosophy_list, 'history': history_list, 'about': about_list}
    return mission_list, curriculum_list, philosophy_list, history_list, about_list


In [46]:
if Debug:
    print("Output of categorize_page:\n\n", categorize_page(example_textlist), "\n\n")


Output of categorize_page:

 (['Admissions', 'Mission', 'It is the mission of 21st Century Public Academy to continually search for positive learning experiences that enrich students and staff. Whenever possible, these lessons will take place in the arena in which they are practiced.'], ['21st Century is a charter middle school. We have been a school since 2000. We serve a diverse population of nearly 70 students per grade. All staff bring years of teaching experience into our classrooms, and many have worked together in other settings. We emphasize the core curriculum of Math, Science, Social Studies, and Language Arts, as well as learning experiences in the community, city, and state. Two Associated Arts courses are offered to each student every semester, including music and media programs.'], [], ['History'], ['Admissions', '21st Century is a charter middle school. We have been a school since 2000. We serve a diverse population of nearly 70 students per grade. All staff bring years 

In [ ]:
def find_best_categories(folder_path):
    
    """Parse through all HTML files in foldername to find and save best pages for each category: 
    mission, curriculum, philosophy, history, about/general self-description."""
    
    list_pages = [file for file in glob(folder_path + "**", recursive=True) if file.endswith(".html")] # Keep only HTML files
    num_pages = len(list_pages)
    max_page_score = (-1, -1)
    
    for i in range(num_pages):
        page_text = parsefile_by_tags(list_pages[i])

        if len(page_text) != 0:
            page_score = dict_match(page_text, custom_dict) / len(page_text.split())
            if page_score > max_page_score[0]:
                max_page_score = (page_score, i)
    max_text = open(filtered_file_format.format(max_page_score[1])).read()
    
    print("Page with the highest dictionary score:\n\n" + max_text)
    
    return mission_page,curr_page,phil_page,hist_page,about_page

In [ ]:
if Debug:
    print("Output of find_best_categories:\n\n", find_best_categories(example_folder), "\n\n" )
    

In [66]:
def parse_school(school_dict, school_name, school_address, school_URL, datalocation, iter, numschools):
    
    """Parses webtext for a given school, using helper functions to run analyses and then saving multiple outputs to school_dict:
    full (partially cleaned) webtext, by parsing webtext of each .html file (removing inline tags, etc.) within school's folder, via parsefile_by_tags();
    filtered webtext, by keeping only those parsed text elements containing a keyword in previously defined keywords list, via filter_keywords_page();
    parsed webtext, having removed overlapping headers/footers common to multiple pages, via remove_overlaps();
    all text associated with specific categories by filtering webtext according to keywords for 
    mission, curriculum, philosophy, history, and about/general self-description, via categorize_page(); and
    contents of those individual pages best matching each of these categories, via find_best_categories."""
    
    iter+=1
    print("Parsing " + str(school_name) + ", which is school #" + str(iter) + " of " + str(numschools) + "...")
    
    school_dict['mission'],school_dict['curriculum'],school_dict['philosophy'],school_dict['history'],school_dict['about'] = "","","","",""
    school_dict['mission_best'],school_dict['curriculum_best'],school_dict['philosophy_best'],school_dict['history_best'],school_dict['about_best'] = "","","","",""
    school_dict["webtext"], school_dict["parsed_text"], school_dict["filtered_text"], school_dict["duplicate_flag"], school_dict["parse_error_flag"] = [], [], [], 0, 0
    
    folder_name = re.sub(" ","_",(name+" "+address[-8:-6]))
    school_folder = datalocation + folder_name + "/"
    
    if school_URL not in parsed: #check if this URL has already been parsed. If so, skip this school to avoid duplication bias
        parsed+=school_URL
        
        try:
            for file in glob(school_folder + "**", recursive=True) if file.endswith(".html"): 
                # Parse file only if it contains HTML. This is easy: wget gave the ".html" file extension to appropriate files when downloading
                #if bool(BeautifulSoup(open(fname), bsparser).find())==True: # More inefficient way to check if file contains HTML, for data not downloaded by wget
                if Debug:
                    print("    Parsing HTML in " + str(file) + "...")
                try:                    
                    parsed_pagetext = parsefile_by_tags(file) # Parse page text (filter too?)
                    school_dict["webtext"].extend(parsed_pagetext) # Add new parsed text to long list

                    mission_text,curr_text,phil_text,hist_text,about_text = "","","","","" # Initialize new additions to school's categories
                    mission_text,curr_text,phil_text,hist_text,about_text = categorize_page(parsed_pagetext) # Parse page text into the five categories
                    school_dict['mission'].extend(mission_text) # Add new text to categories for school
                    school_dict['curriculum'].extend(curr_text)
                    school_dict['philosophy'].extend(phil_text)
                    school_dict['history'].extend(hist_text)
                    school_dict['about'].extend(about_text)
                        
                    school_dict["filtered_text"].extend(filter_keywords_page(parsed_pagetext)) # Filter parsed file using keywords list
                        
                    if Debug:
                        print("    Successfully parsed & categorized file...\n\n")
                        
                except Exception as e:
                    if Debug:
                        print("      ERROR! Failed to parse & categorize file...")
                        print("      ",e)
                    else:
                        continue
                              
            print("  Successfully parsed & categorized website text...\n\n")

        except Exception as e:
            print("    ERROR! Failed to parse & categorize webtext of " + str(school_name))
            print("    ",e)
            school_dict["parse_error_flag"] = 1
    
        try:
            # Filter out overlapping parts of each page, save full string in dict element "parsed_text":
            school_dict["parsed_text"] = parse_remove_overlaps(school_folder, folder_name)
            
            # Find and save best pages for each of the five categories:
            mission_best,curr_best,phil_best,hist_best,about_best = "","","","","" # Initialize new dict elements
            mission_best,curr_best,phil_best,hist_best,about_best = find_best_categories(school_folder) # Parse page text into the five categories
            school_dict['mission_best'].extend(mission_best)
            school_dict['curriculum_best'].extend(curr_best)
            school_dict['philosophy_best'].extend(phil_best)
            school_dict['history_best'].extend(hist_best)
            school_dict['about_best'].extend(about_best)
            
        except Exception as e:
            print("    ERROR! Failed to remove overlaps & find best pages while parsing webtext of " + str(school_name))
            print("    ",e)
            school_dict["parse_error_flag"] = 1
            return
    
    else:
        print("DUPLICATE URL DETECTED. Skipping " + str(school_name) + "...\n\n")
        school_dict["duplicate_flag"] = 1
        return
    
    print("SUCCESS! Parsed, categorized, and removed overlaps from website text for " + str(school_name) + "...\n\n")
    return


In [47]:
# ### Preparing data to be parsed

# set charter school data file and corresponding varnames:
if Debug:
    data_loc = micro_sample13 # Run on micro-sample first, for debugging purposes
else:
    data_loc = full_schooldata # Run at scale using URL list of full charter population
URL_var,NAME_var,ADDR_var = get_vars(data_loc) # get varnames depending on data source

itervar = 0 # initialize iterator that counts number of schools already parsed
parsed = [] # initialize list of URLs that have already been parsed
dicts_list = [] # initialize list of dictionaries to hold school data

# Create dict list from CSV on file, with one dict per school
with open(data_loc, 'r', encoding = 'Latin1') as csvfile: # open data file
    reader = csv.DictReader(csvfile) # create a reader
    for row in reader: # loop through rows
        dicts_list.append(row) # append each row to the list
        
# Note on data structures: each row, dicts_list[i] is a dictionary with keys as column name and value as info.
# This will be translated into pandas data frame once (rather messy) website text is parsed into consistent variables

In [ ]:
# ### Run parsing algorithm on schools

test_dicts = dicts_list[0] # Limit number of schools to analyze, in order to refine methods

if Debug:
    for school in test_dicts:
        parse_school(school, school[NAME_var], school[ADDR_var], school[URL_var], data_loc, itervar, len(dicts_list))
        
else:
    for school in dicts_list:
        parse_school(school, school[NAME_var], school[ADDR_var], school[URL_var], data_loc, itervar, len(dicts_list))

In [ ]:
# Check out results:
if Debug:
    print(test_dicts[0])
else:
    print(dicts_list[0])
    

In [ ]:
# Save output:
if Debug:
    dictfile = "testing_dicts_" + str(datetime.today())
    save_to_file(test_dicts, save_dir+dictfile, "JSON")
else:
    dictfile = "school_dicts_" + str(datetime.today())
    save_to_file(dicts_list, save_dir+dictfile, "JSON")
